## Required Imports

In [539]:
import h5py
import matplotlib.pyplot as plt
import json
import numpy as np
import plotly.graph_objects as go
import lmfit as lm

from common import save_to_igor_itx, calculate_fit, i_sense, entropy_weak, get_data_index, bin_data

from squarewave import process_per_row_parts, SquareProcessedData, process_avg_parts, get_data_part, single_wave_masks, convert_to_4_setpoint_AW

## Data -- Square Wave Parts

In [552]:
datnum = 2164
with h5py.File(f'data/dat{datnum}.h5', 'r') as f:
    data = f['cscurrent_2d'][:]
    data_x = f['x_array'][:]
    sweeplogs = f['metadata'].attrs['sweep_logs']
    aw = f['fdAW_0'][:]
    data_y = f['y_array'][:]
sweeplogs = json.loads(sweeplogs)
awg_info = sweeplogs['FastDAC 1']['AWG']
num_pts = awg_info['waveLen']
num_steps = awg_info['numSteps']
duration = num_pts/awg_info['measureFreq']
measure_freq = sweeplogs['FastDAC 1']['MeasureFreq']
x = np.linspace(0, duration, num_pts)
data_x = np.linspace(data_x[0], data_x[-1], num_steps)
aw = convert_to_4_setpoint_AW(aw)
data = np.mean(data, axis=0)

In [553]:
awg_info
aw

array([[  0.,  30.,   0., -30.],
       [ 51.,  51.,  51.,  51.]], dtype=float32)

In [554]:
# sweeplogs

In [555]:
bin_size = 1  # Binning after processing before plotting

x = bin_data(x, bin_x=bin_size)

In [556]:
data_x.shape, data[round(num_pts/8)::num_pts].shape

((498,), (498,))

In [557]:
fig = go.Figure()
d1 = data[round(num_pts/8)::num_pts]
d2 = data[round(num_pts*3/8)::num_pts]
fig.add_trace(go.Scatter(x=data_x, y=d1, mode='lines'))
fig.add_trace(go.Scatter(x=data_x, y=d2, mode='lines'))

fig.add_trace(go.Scatter(x=data_x, y=d1-d2, mode='lines'))
fig.show()

#### Average data for different parts of square wave applied

In [558]:
peak = -14  # peak position in mV  (before averaging)
dip = 2   # dip position in mV   (before averaging)
width = 5  # + - this value averaged around the peak/dip in mV
# peak = -73  # peak position in mV
# dip = 35   # dip position in mV
# width = 30  # + - this value averaged around the peak/dip in mV

widx = round(width/np.mean(np.diff(data_x)))
peak_idx, dip_idx = get_data_index(data_x, [peak, dip], is_sorted=True)
regions = np.s_[0:widx*2], np.s_[peak_idx-widx:peak_idx+widx], np.s_[dip_idx-widx: dip_idx+widx], np.s_[-widx*2:-1]

all_avg = np.reshape(data, (-1, num_pts))  # Line up all square wave cycles on top of each other
region_names = ('zeroL', 'pos', 'neg', 'zeroR')
masks = single_wave_masks(aw)

In [559]:
avgs = list()
setpoint_averaging_delay_ms = 3  # How many ms to throw out before averaging setpoint values
setpoint_start_index = round(setpoint_averaging_delay_ms/1000*measure_freq)
print(f'Setpoint start index = {setpoint_start_index}')

for region, name in zip(regions, region_names):
    print(region)
    avg = np.mean(all_avg[region], axis=0)
    avg = avg - np.mean([np.nanmean((avg*masks[0])[setpoint_start_index:]), np.nanmean((avg*masks[2])[setpoint_start_index:])])
    avgs.append(avg)
    
datas = dict()
for avg, name in zip(avgs, region_names):
    datas[name] = list()
    for mask in masks:
        data = avg*mask
        data = bin_data(data, bin_x=bin_size)
        datas[name].append(data) 
        
        

Setpoint start index = 8
slice(0, 12, None)
slice(225, 237, None)
slice(245, 257, None)
slice(-12, -1, None)


## Quick plot before exporting data to Igor for final Figure

In [560]:
for name, data in datas.items():
    fig = go.Figure()
    
    fig.update_layout(xaxis_title='Time through Square Wave /s', yaxis_title=f'Current /nA',
                                  title=f'Data averaged to one Square Wave')
        
    for d, label in zip(data, ['00', '+', '01', '-']):
        fig.add_trace(go.Scatter(y=d, x=x, mode='lines', name=label))
    fig.show()

## Save to .itx file for final Figure in Igor

In [561]:
np.array(list(datas.values())).reshape((16, -1)).shape

(16, 204)

In [562]:
save_to_igor_itx(f"exports/SWData.itx",
                 xs=[x]*4*4,
                 datas=list(np.array(list(datas.values())).reshape((4*4, -1))),
                 names=[f'SWData_{name}_{label}' for name in datas.keys() for label in ['v0_0', 'vP', 'v0_1', 'vM']])

## Data -- Hot Cold transition

In [493]:
# # Calculate Delta T from DC heating measurements
# datnums = 2143, 2148, 2149  # 0, +, -ve 3nA heating current
# fit_range = -0.4, 0.2
# dc_thetas = {}
# for num in datnums:
#     with h5py.File(f'data/dat{num}.h5', 'r') as f:
#         data = f['cscurrent_2d'][:]
#         x = f['x_array'][:]/100  # Convert to real mV
#         sweeplogs = f['metadata'].attrs['sweep_logs']
#
#     # fig = go.Figure()
#     # temp_x = bin_data(x, bin_x=10)
#     # temp_data = bin_data(data, bin_x=10)
#     # fig.add_trace(go.Heatmap(x=temp_x, z=temp_data))
#     # fig.show()
#
#     params = lm.Parameters()
#     params.add_many(
#         ('mid', 0, True, None, None, None, None),
#         ('theta', 20/100, True, 0.01, None, None, None),
#         ('amp', 1, True, 0, None, None, None),
#         ('lin', 0.005/100, True, 0, None, None, None),
#         ('const', 5, True, None, None, None, None)
#     )
#
#     indexs = get_data_index(x, fit_range, is_sorted=True)
#     indexs = np.s_[indexs[0]:indexs[1]]
#     fits = [calculate_fit(x[indexs], d[indexs], params, func=i_sense) for d in data]
#
#     thetas = [fit.params['theta'].value for fit in fits]
#     dc_thetas[num] = thetas, np.mean(thetas), np.std(thetas)/np.sqrt(len(thetas))
#
# dc_thetas = {
#     'cold': dc_thetas[2143],
#     'positive': dc_thetas[2148],
#     'negative': dc_thetas[2149],
# }
#
# dc_delta_T = (dc_thetas['positive'][1]+dc_thetas['negative'][1])/2 - dc_thetas['cold'][1]
# dc_delta_T_mk = dc_delta_T*100/dc_thetas['cold'][1]  # 100mK fridge temp

In [494]:
# for k in dc_thetas:
#     print(k, dc_thetas[k][1], dc_thetas[k][2])

In [495]:
datnum = 2164
with h5py.File(f'data/dat{datnum}.h5', 'r') as f:
    data = f['cscurrent_2d'][:]
    x = f['x_array'][:]/100  # Convert to real mV
    sweeplogs = f['metadata'].attrs['sweep_logs']
    aw = f['fdAW_0'][:]
sweeplogs = json.loads(sweeplogs)
awg_info = sweeplogs['FastDAC 1']['AWG']
num_pts = awg_info['waveLen']
num_steps = awg_info['numSteps']
# measure_freq = sweeplogs['measureFreq']
measure_freq = sweeplogs['FastDAC 1']['MeasureFreq']
aw = convert_to_4_setpoint_AW(aw)

In [496]:
temp_data = bin_data(data, bin_x=100)
temp_x = bin_data(x, bin_x=100)
fig = go.Figure()
fig.add_trace(go.Heatmap(x=temp_x, z=temp_data))
fig.show()

In [497]:
setpoint_averaging_delay_ms = 8  # How many ms to throw out before averaging setpoint values
row_fit_range = -50, 36  # ACC*100 mV to fit between (raw)
average_fit_width = 45  # +- this width in ACC*100 to fit (after averaging and centering)



setpoint_start_index = round(setpoint_averaging_delay_ms/1000*measure_freq)
print(f'Setpoint start index = {setpoint_start_index}')
processed = process_per_row_parts(x=x, data=data, arbitrary_wave=aw, setpoint_start=setpoint_start_index, num_steps=num_steps,num_cycles=1)
cold_data = get_data_part(processed.cycled, 'cold')

Setpoint start index = 20


In [498]:
params = lm.Parameters()
params.add_many(
    ('mid', 0, True, None, None, None, None),
    ('theta', 20/100, True, 0.01, None, None, None),
    ('amp', 1, True, 0, None, None, None),
    ('lin', 0.005/100, True, 0, None, None, None),
    ('const', 5, True, None, None, None, None)
)

indexs = get_data_index(x, row_fit_range, is_sorted=True)
indexs = np.s_[indexs[0]:indexs[1]]
fits = [calculate_fit(x[indexs], d[indexs], params, func=i_sense) for d in data]

centers = [fit.params['mid'].value for fit in fits]

In [499]:
processed = process_avg_parts(processed, centers)

In [500]:
x = processed.x
cold = get_data_part(processed.averaged, 'cold')  # Average unheated
hot = get_data_part(processed.averaged, 'hot')  # Average heated
v0_0 = get_data_part(processed.averaged, 0)  # First unheated
vp = get_data_part(processed.averaged, 1)  # Heating with positive bias
v0_1 = get_data_part(processed.averaged, 2)  # Second unheated
vm = get_data_part(processed.averaged, 3)  # Heating with negative bias

entropy = processed.average_entropy_signal

indexs = get_data_index(x, [-average_fit_width, average_fit_width], is_sorted=True)
indexs = np.s_[indexs[0]:indexs[1]]


In [501]:
cold_fit = calculate_fit(x[indexs], cold[indexs], params=params, func=i_sense)
hot_fit = calculate_fit(x[indexs], hot[indexs], params=params, func=i_sense)

entropy_params = lm.Parameters()
entropy_params.add_many(
    ('mid', 0, True, None, None, None, None),
    ('theta', 10/100, True, 0, 500, None, None),
    ('const', 0, False, None, None, None, None),
    ('dS', 0, True, -5, 5, None, None),
    ('dT', 5, True, -10, 50, None, None)
)

entropy_fit = calculate_fit(x[indexs], entropy[indexs], params=entropy_params, func=entropy_weak)

amplitude = cold_fit.params['amp'].value
hot_theta = hot_fit.params['theta'].value
cold_theta = cold_fit.params['theta'].value

hot_theta_err = hot_fit.params['theta'].stderr
cold_theta_err = cold_fit.params['theta'].stderr

print(f'Hot theta = {hot_theta:.6f} +- {hot_theta_err:.6f}')
print(f'Cold theta = {cold_theta:.6f} +- {cold_theta_err:.6f}')


Hot theta = 0.048458 +- 0.000088
Cold theta = 0.037836 +- 0.000055


In [502]:

delta_T =  hot_theta - cold_theta  # Delta T from Hot fit - Cold Fit
# delta_T = 0.01111
delta_x = np.mean(np.diff(x))  # Steps are all equal size
scaling = delta_x/amplitude/delta_T
integrated = np.nancumsum(entropy, axis=-1) * scaling

In [503]:
print(f'100mK Theta = {cold_theta:.6f} mV\n'
      f'Heated Theta = {hot_theta:.6f} mV\n'
      f'Delta T from direct fitting = {delta_T:.6f} mV = {delta_T*100/cold_theta:.6f} mK\n'
      # f'Delta T from DC bias = {dc_delta_T:.4f} mV = {dc_delta_T_mk:.4f} mK\n'
      )

100mK Theta = 0.037836 mV
Heated Theta = 0.048458 mV
Delta T from direct fitting = 0.010622 mV = 28.073010 mK



In [504]:

delta_T =  hot_theta - cold_theta  # Delta T from Hot fit - Cold Fit
# delta_T = 0.01111
delta_x = np.mean(np.diff(x))  # Steps are all equal size
scaling = delta_x/amplitude/delta_T
integrated = np.nancumsum(entropy, axis=-1) * scaling

In [505]:
print(f'100mK Theta = {cold_theta:.3f} mV\n'
      f'Heated Theta = {hot_theta:.3f} mV\n'
      f'Delta T from direct fitting = {delta_T:.4f} mV = {delta_T*100/cold_theta} mK\n'
      f'Delta T from DC bias = \n'
      )

In [506]:
entropy_fit

## Quick plot before exporting data to Igor for final Figure

In [507]:
x, v0_0, v0_1, vm, vp, entropy, integrated = [bin_data(arr, bin_x=3) for arr in [x, v0_0, v0_1, vm, vp, entropy, integrated]]

In [508]:
fig = go.Figure()
fig.update_layout(title='Hot/Cold transition')
fig.add_trace(go.Scatter(x=x, y=v0_0, mode='markers', marker=dict(color='blue', symbol='circle-open')))
fig.add_trace(go.Scatter(x=x, y=v0_1, mode='markers', marker=dict(color='blue', symbol='cross')))
fig.add_trace(go.Scatter(x=x, y=cold_fit.eval(x=x), mode='lines', line=dict(color='blue')))

fig.add_trace(go.Scatter(x=x, y=vp, mode='markers', marker=dict(color='red', symbol='circle-open')))
fig.add_trace(go.Scatter(x=x, y=vm, mode='markers', marker=dict(color='red', symbol='cross')))
fig.add_trace(go.Scatter(x=x, y=hot_fit.eval(x=x), mode='lines', line=dict(color='red')))
fig

In [509]:
fig = go.Figure()
fig.update_layout(title='Entropy signal')
fig.add_trace(go.Scatter(x=x, y=entropy, mode='markers', marker=dict(symbol='circle-open')))
fig.add_trace(go.Scatter(x=x, y=entropy_fit.eval(x=x), mode='lines'))
fig

In [510]:
fig = go.Figure()
fig.update_layout(title='Integrated Entropy')
fig.add_trace(go.Scatter(x=x, y=integrated, mode='markers', marker=dict(symbol='circle-open')))
fig.add_shape(dict(type='line', yref='y', y0=np.log(2), y1=np.log(2), xref='paper', x0=0, x1=1,
                  line=dict(color='black', dash='dash')))
fig.add_shape(dict(type='line', yref='y', y0=np.log(3), y1=np.log(3), xref='paper', x0=0, x1=1,
                  line=dict(color='black', dash='dash')))
fig

## Save to .itx file for final Figure in Igor

In [510]:
# save_to_igor_itx(f"exports/WCGW_SWData_{name}.itx", [x]*4, data, [f'WCGW_SWData_{name}_{label}' for label in ['v0_0', 'vP', 'v0_1', 'vP']])
save_to_igor_itx(f'exports/Transition_data.itx',
                 xs=[x]*6,
                 datas=[v0_0, v0_1, cold_fit.eval(x=x), vp, vm, hot_fit.eval(x=x)],
                 names=['trans_00', 'trans_01', 'trans_fit_cold', 'trans_vp', 'trans_vm', 'trans_fit_hot'])

save_to_igor_itx(f'exports/Entropy_data.itx',
                 xs=[x]*3,
                 datas = [entropy, entropy_fit.eval(x=x), integrated],
                 names=['entropy_signal', 'entropy_fit', 'integrated_entropy']
)